In [31]:
import numpy as np
import pandas as pd
from scipy.sparse import csr_matrix
import sklearn
from sklearn.datasets import fetch_20newsgroups
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score
from sklearn.cross_validation import train_test_split
from sklearn.feature_extraction.text import TfidfTransformer, CountVectorizer, HashingVectorizer

# 1. Работа с категориальными признками

Все эксперименты в этой лабораторной работе предлагается проводить на данных соревнования Amazon Employee Access Challenge: https://www.kaggle.com/c/amazon-employee-access-challenge

В данной задаче предлагается предсказать, будет ли одобрен запрос сотрудника на получение доступа к тому или иному ресурсу. Все признаки являются категориальными.

Данные доступны по ссылке https://www.dropbox.com/s/q6fbs1vvhd5kvek/amazon.csv

Для оценки качества используется ROC-AUC

In [27]:
data = pd.read_csv('amazon.csv')
data.head()

ACTION  RESOURCE  MGR_ID  ROLE_ROLLUP_1  ROLE_ROLLUP_2  ROLE_DEPTNAME  \
0       1     39353   85475         117961         118300         123472   
1       1     17183    1540         117961         118343         123125   
2       1     36724   14457         118219         118220         117884   
3       1     36135    5396         117961         118343         119993   
4       1     42680    5905         117929         117930         119569   

   ROLE_TITLE  ROLE_FAMILY_DESC  ROLE_FAMILY  ROLE_CODE  
0      117905            117906       290919     117908  
1      118536            118536       308574     118539  
2      117879            267952        19721     117880  
3      118321            240983       290919     118322  
4      119323            123932        19793     119325

In [28]:
data.shape

(32769, 10)

In [29]:
X_train, X_test, y_train, y_test = train_test_split(data.iloc[:, 1:], data.iloc[:, 0],
                                                    test_size=0.3, random_state=241)

### Подзадача 1.0 (Опционально)
Воспользуйтесь любым известным вам методом классификации для предсказания на данных без предобработки. Какое максимальное качество (roc_auc_score) удаётся получить?

### Подзадача 1.1
Для каждого признака посчитайте число уникальных значений в датасете. Посчитайте также долю объектов каждого класса.

Считайте статистики по оригинальному датасету, а не только по train части. 

Сохраните результат в dict

### Подзадача 1.2
Напишите функцию one_hot_decode(), которая преобразовывает dataframe с категориальными признаками в sparse-матрицу (scipy.sparse.csr_matrix) с one_hot представлениями для всех признаков.

Для создания разреженной матрицы необходимо воспользоваться наиболее эффективным конструктором csr_matrix, нигде не храня полную матрицу.

In [34]:
def one_hot_decode(X, vector_size_dict=None):
    return csr_matrix(([17, 19, 42], ([1, 0, 0], [0, 1, 0])))

print(one_hot_decode(data.iloc[:, 1:]).todense())

[[42 19]
 [17  0]]


### Позадача 1.3
Обучите логистическую регрессию на получившихся признаках. Попробуйте l1 и l2 резугялирзацию. Постройте график зависимости качества на обучающей и тестовой выборках в зависимости от значения коэффициента регуляризации. (Попробуйте значения от 0.001 до 1000 по лог-шкале) Какое наилучшее качество удалось получить на отложенной выборке?

### Позадача 1.4 (Бонус)
Напишите функцию feature_hashing_decode(), которая преобразовывает dataframe с категориальными признаками в sparse-матрицу (scipy.sparse.csr_matrix) с one-hot представлениями для всех признаков, где индекс единицы в one-hot представлении задаётся как хэш-функция от значения категориального признака по модулю $h$, где $h$ – индивидуально для каждого признака и задаётся словарём vector_size_dict.

In [35]:
def feature_hashing_decode(X, vector_size_dict=None):
    return csr_matrix(([17, 19, 42], ([1, 0, 0], [0, 1, 0])))

print(feature_hashing_decode(data.iloc[:, 1:]).todense())

[[42 19]
 [17  0]]


# 2. Работа с текстами
20 newsgroups – задача рубрикации текстов. 

Смысл в том, чтобы научиться по тексту новостного объвления предсказывать его рубрику. 

Информация о наличии или отсутствии тех или иных слов в тексте является информативным признаком о его рубрике.

In [37]:
data = fetch_20newsgroups(remove=('headers', 'footers', 'quotes'))
X_train, y_train = data['data'], data['target']
data = fetch_20newsgroups(remove=('headers', 'footers', 'quotes'), subset='test')
X_test, y_test = data['data'], data['target']

### Рубрики

In [19]:
data['target_names']

['alt.atheism',
 'comp.graphics',
 'comp.os.ms-windows.misc',
 'comp.sys.ibm.pc.hardware',
 'comp.sys.mac.hardware',
 'comp.windows.x',
 'misc.forsale',
 'rec.autos',
 'rec.motorcycles',
 'rec.sport.baseball',
 'rec.sport.hockey',
 'sci.crypt',
 'sci.electronics',
 'sci.med',
 'sci.space',
 'soc.religion.christian',
 'talk.politics.guns',
 'talk.politics.mideast',
 'talk.politics.misc',
 'talk.religion.misc']

### Пример пары объект-рубрика в обучающей выборке

In [39]:
object_idx = 117
print(data['target_names'][y[object_idx]])
print('----------')
print(X[object_idx])

sci.crypt
----------

Where?  I honestly didn't see any...


I disagree, if for no other reason than that there are already other 
standards in place.  Besides, even if they restrict encryption on the NREN, 
who cares?  Most of the Internet is commercial anyway.  The NREN is only for 
geovernment and university research (read the proposals--it's a "data 
superhighway" for Cray users, not anything having to do with the Internet).



### Задание №2.1

1. Перевести во всех документах все буквы в нижний регистр. Заменить во всех документах символы, не являющиеся буквами и цифрами, на пробелы. Полезные функции: .lower, .isalnum.
2. Разбить каждый документ на термы по пробельным символам (пробелы, переносы строки). Полезная функция: .split()
3. Преобразовать датасет в разреженную матрицу scipy.sparse.csr_matrix, где значение x в позиции (i, j) означает, что в документе i слово j встретилось x раз. (Воспользуйтесь sklearn.feature_extraction.text.CountVectorizer)
5. Произвести tf-idf преобразование датасета при помощи sklearn.feature_extraction.text.TfidfTransformer. Используйте параметры по умолчанию.
6. Обучите логистическую регрессию на получившихся признаках. Подберите коэффициент регуляризации по значению ошибки на тестовой выборке.

### Задание № 2.2 (Бонус)

Попробуйте улучшить качество с помощью каких-нибудь ещё признаков, посчитанных по данным. (Попробуйте, например, добавить усреднённые word2vec представления новостных заголовков)